<a href="https://colab.research.google.com/github/cristianmejia00/clustering/blob/main/06_heatmap_sankey/01_heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Heatmap for Topic Modeling with BERTopic


# Requirements

## Packages installation and initialization

In [1]:
!pip install bertopic[visualization]

zsh:1: no matches found: bertopic[visualization]


In [2]:
import pandas as pd
import time
import math
from datetime import date
import uuid
import re
import os
import json
import pickle
from itertools import compress
from bertopic import BERTopic
from umap import UMAP
from gensim.parsing.preprocessing import remove_stopwords
import numpy as np
from sklearn.cluster import KMeans

/Users/cristian/Desktop/GitHub/clustering/env-tm/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [21]:
# Change to the name of the folder in your Google Drive
root_folder_name = 'Bibliometrics_Drive'
#ROOT_FOLDER_PATH = f"drive/MyDrive/{root_folder_name}" # <- Google Colab
ROOT_FOLDER_PATH = f"/Users/cristian/Library/CloudStorage/GoogleDrive-cristianmejia00@gmail.com/My Drive/{root_folder_name}" #Mac

## Connect your Google Drive

In [22]:
# from google.colab import drive
# drive.mount('/content/drive')

In [4]:
# Function to save object to a pickle file
def save_object_as_pickle(obj, filename):
  """
  Saves an object as a pickle file.

  Args:
      obj: The object to be saved.
      filename: The filename of the pickle file.
  """
  with open(filename, "wb") as f:
    pickle.dump(obj, f)



In [5]:
# Function to load pickle object given a path
def load_pickle(path):
    with open(path, 'rb') as f:
        return pickle.load(f)


In [6]:
def save_heatmap_settings_as_json(heatmap_settings, filename="heatmap_settings.json"):
  """Saves heatmap settings as a JSON file with pretty indentation.

  Args:
      heatmap_settings: The heatmap settings dictionary.
      filename: The name of the JSON file.
  """
  with open(filename, "w") as f:
    json.dump(heatmap_settings, f, indent=4)



---



## PART 3: Merging Topic Models

# 🔴 Input files and options



In [23]:
heatmap_settings = {
    'metadata': {
      'heatmap_analysis_id': 'H010',
      'heatmap_name': 'Human_Aug-Robotics',
      'date': '2025-01-05',
      'created_by': 'cristianmejia00@gmail.com',
      'notes': '',
      'input_directory': '',
      'output_directory': ''
    },
    'global': {
                'min_cluster_size': 10,
                'seed': 100,
                'transformer_model': 'all-MiniLM-L6-v2',
                'sankey_threshold': 0.8
              },
    'inputs': [
        {
            'project_folder_name': 'Q321_TI_robot',
            'analysis_folder_name': 'a01_cn__f01_dc__c01_lv',
            'level_folder_name': 'level1',
            'embeddings_folder_name': 'f01/e01',
            'display_name': 'RBT',
            'cluster_column': 'Cluster Code',
            'heatmap_display_order': 0,
            'sankey_display_order': 1,
            'color': "#E9571F"
        },
        {
            'project_folder_name': 'Q318_human_augmentation',
            'analysis_folder_name': 'a01_cn__f01_dc__c01_lv',
            'embeddings_folder_name': 'f01/e01',
            'level_folder_name': 'level1',
            'display_name': 'HA',
            'cluster_column': 'Cluster Code',
            'heatmap_display_order': 1,
            'sankey_display_order': 0,
            'color': '#808080'
        }#,
        # {
        #     'project_folder_name': 'Q282b_riken_com',
        #     'analysis_folder_name': 'a01_tm__f01_e01__km01',
        #     'embeddings_folder_name': 'f01/e01',
        #     'level_folder_name': 'level0',
        #     'display_name': 'RIKEN.Com',
        #     'cluster_column': 'Cluster Code',
        #     'heatmap_display_order': 3,
        #     'sankey_display_order': 2,
        #     'color': '#808080'
        # },
        # {
        #     'project_folder_name': 'Q312_utokyo',
        #     'analysis_folder_name': 'a01_tm__f01_e01__km01',
        #     'embeddings_folder_name': 'f01/e01',
        #     'level_folder_name': 'level0',
        #     'display_name': 'UTokyo',
        #     'cluster_column': 'Cluster Code',
        #     'heatmap_display_order': 4,
        #     'sankey_display_order': 1,
        #     'color': '#F2BA05'
        # }#,
        # # {
        # #     'project_folder_name': 'Q308_bio_plant',
        # #     'analysis_folder_name': 'a01_tm__f01_e01__km01',
        # #     'embeddings_folder_name': 'f01/e01',
        # #     'level_folder_name': 'level0',
        # #     'display_name': 'Plant',
        # #     'cluster_column': 'Cluster Code',
        # #     'heatmap_display_order': 4,
        # #     'sankey_display_order': 1,
        # #     'color': '#66FF00'
        # # }
      ]
}

In [12]:
# analysis_folder = ""

# if not os.path.exists(analysis_folder):
#   print("We are here!")
#   !mkdir $analysis_folder


# # Save settings
# save_heatmap_settings_as_json(heatmap_settings, filename=f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}/heatmap_settings_{heatmap_settings["metadata"]["heatmap_analysis_id"]}_{heatmap_settings["metadata"]["heatmap_name"]}.json')

In [54]:
# analysis_folder = f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}'

# if not os.path.exists(analysis_folder):
#   !mkdir $analysis_folder

mkdir: /Users/cristian/Library/CloudStorage/GoogleDrive-cristianmejia00@gmail.com/My: Permission denied
mkdir: Drive/Bibliometrics_Drive: No such file or directory


In [62]:

# Save settings
save_heatmap_settings_as_json(heatmap_settings, filename=f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}/heatmap_settings_{heatmap_settings["metadata"]["heatmap_analysis_id"]}_{heatmap_settings["metadata"]["heatmap_name"]}.json')

In [24]:
heatmap_input_dfs = []
for tm in heatmap_settings['inputs']:
  document_path = f'{ROOT_FOLDER_PATH}/{tm["project_folder_name"]}/{tm["analysis_folder_name"]}/{tm["level_folder_name"]}/article_report.csv'
  print(document_path)
  input_df = pd.read_csv(document_path,
                         usecols=['ID', 'uuid', tm['cluster_column']])
  # Each dataset can use different clustering result e.g. X_C, level0, level1, so we need to unify the header name for concatenation
  input_df['display_name'] = tm['display_name']
  input_df['cluster'] = input_df['display_name'] + "-" + input_df[tm['cluster_column']].astype(str)
  input_df = input_df.rename(columns={'ID': 'UT'})
  input_df = input_df.drop(columns=[tm['cluster_column']])
  heatmap_input_dfs.append(input_df)

/Users/cristian/Library/CloudStorage/GoogleDrive-cristianmejia00@gmail.com/My Drive/Bibliometrics_Drive/Q321_TI_robot/a01_cn__f01_dc__c01_lv/level1/article_report.csv
/Users/cristian/Library/CloudStorage/GoogleDrive-cristianmejia00@gmail.com/My Drive/Bibliometrics_Drive/Q318_human_augmentation/a01_cn__f01_dc__c01_lv/level1/article_report.csv


In [25]:
document_info = pd.concat(heatmap_input_dfs).reset_index(drop=True)
print(len(document_info))
document_info.head()

69838


UT                                  uuid display_name  \
0  WOS:000727032200001  8ef0ae3a-31e2-4bcf-bdc1-c92eb5073877          RBT   
1  WOS:000527746500001  d36cc41d-a318-4e7e-97bd-134806b3461c          RBT   
2  WOS:000835427800001  cc6ec9b2-b9ea-4550-b5d8-cfdd1bf8d9e3          RBT   
3  WOS:000754278900001  82fd0433-5a99-4b1e-8292-7273277c6784          RBT   
4  WOS:000731147700062  77972640-4cd9-42be-9aab-a513d91f2246          RBT   

      cluster  
0  RBT-1-1---  
1  RBT-1-1---  
2  RBT-1-1---  
3  RBT-1-1---  
4  RBT-1-1---



---



## PART 5. Heatmap

In [26]:
# For firms we know, simply get the embeddings back.
embeddings_list = []
corpus_list = []
for tm in heatmap_settings['inputs']:
  print(f"=================Loading: {tm['project_folder_name']}")
  embeddings = load_pickle(f"{ROOT_FOLDER_PATH}/{tm['project_folder_name']}/{tm['embeddings_folder_name']}/embeddings.pck")
  if type(embeddings) == dict:
    print('Dict type found')
    embeddings = embeddings['embeddings']
  corpus_tmp = pd.read_csv(f"{ROOT_FOLDER_PATH}/{tm['project_folder_name']}/{tm['embeddings_folder_name']}/corpus.csv")

  embeddings_list.append(embeddings)
  corpus_list.append(corpus_tmp)

=================Loading: Q321_TI_robot
Dict type found
=================Loading: Q318_human_augmentation
Dict type found


In [27]:
# Combine embeddings
embeddings_uploaded = np.vstack(embeddings_list)
corpus_uploaded = pd.concat(corpus_list).reset_index(drop=True)

In [28]:
embeddings_uploaded.shape

(92987, 384)

In [29]:
print(len(embeddings_uploaded))
print(len(corpus_uploaded))
print(len(document_info))

92987
92987
69838


In [30]:
# prompt: add `embeddings_uploaded` as a column to `corpus_uploaded`
corpus_uploaded['embeddings'] = list(embeddings_uploaded)

In [31]:
# prompt: remove  rows of corpus_uploaded where UT is duplicated

# Remove rows where 'UT' is duplicated, keeping the first occurrence
corpus_uploaded = corpus_uploaded.drop_duplicates(subset=['UT'], keep='first')

In [32]:
# prompt: merge `corpus_uploaded` and `document_info` by column UT. The merged data frame has as many rows and same sorting as corpus_uploaded. The merged data frame is named `full_corpus`.
full_corpus = pd.merge(document_info[['UT', 'uuid', 'cluster']], corpus_uploaded[['UT', 'text', 'embeddings']], on='UT', how='left')

In [33]:
len(full_corpus)

69838

In [34]:
len(document_info)

69838

In [35]:
# prompt: Remove all rows in full_corpus where the size of column `embeddings` do not match 384
full_corpus = full_corpus[full_corpus['embeddings'].apply(lambda x: len(x) == 384 if isinstance(x, list) or isinstance(x, np.ndarray) else False)]

In [36]:
len(full_corpus)

69838

In [37]:
# Remodel the topic model
from bertopic.backend import BaseEmbedder
from bertopic.cluster import BaseCluster
from bertopic.vectorizers import ClassTfidfTransformer
from bertopic.dimensionality import BaseDimensionalityReduction
from sentence_transformers import SentenceTransformer

In [38]:
cluster_idx_mapping = full_corpus.cluster.value_counts()
cluster_idx_mapping = cluster_idx_mapping[cluster_idx_mapping >= heatmap_settings['global']['min_cluster_size']]
cluster_idx_mapping

cluster
RBT-2-1---    1597
RBT-1-1---    1134
RBT-1-2---    1099
RBT-3-1---    1061
RBT-1-3---    1010
              ... 
HA-14-1---      46
HA-13-2---      46
HA-7-2---       46
HA-2-4---       45
HA-12-1---      45
Name: count, Length: 275, dtype: int64

In [39]:
full_corpus = full_corpus[full_corpus.cluster.isin(cluster_idx_mapping.index.to_list())]

In [40]:
len(full_corpus)

69838

In [41]:
# Form the embbedings
my_embeddings = np.vstack(full_corpus['embeddings'].tolist())

In [42]:
# get text and topics
docs = full_corpus.text
cluster_list = full_corpus.cluster

In [43]:
idx_cluster = [cluster_idx_mapping.index.get_loc(i) for i in cluster_list]

In [44]:
len(idx_cluster) == len(docs) == len(my_embeddings)

True

# 🟢🟢

In [45]:
# Init "empty" models
embedding_model = SentenceTransformer(heatmap_settings["global"]["transformer_model"])
empty_dimensionality_model = BaseDimensionalityReduction()
empty_cluster_model = BaseCluster()
ctfidf_model = ClassTfidfTransformer(reduce_frequent_words=True)

# Fit BERTopic without actually performing any clustering
topic_model= BERTopic(
        embedding_model=embedding_model,
        umap_model=empty_dimensionality_model,
        hdbscan_model=empty_cluster_model,
        ctfidf_model=ctfidf_model
)

In [46]:
topics, probs = topic_model.fit_transform(docs, my_embeddings, y=idx_cluster)

In [47]:
tm_summary = topic_model.get_topic_info()
tm_summary

Topic  Count                                    Name  \
0        0   1597            0_older_care_adults_dementia   
1        1   1134      1_continuum_tendon_concentric_tube   
2        2   1099  2_magnetic_soft_actuation_magnetically   
3        3   1061              3_path_rrt_planning_colony   
4        4   1010          4_fish_swimming_underwater_fin   
..     ...    ...                                     ...   
270    270     46     270_mxene_strain_mxenes_stretchable   
271    271     46          271_malate_genes_crispr_tomato   
272    272     46       272_brain_fnirs_notifications_eog   
273    273     45          273_exosuit_ule_shoulder_elbow   
274    274     45    274_symmetrical_hypersonic_dbp_glide   

                                        Representation  \
0    [older, care, adults, dementia, nursing, careg...   
1    [continuum, tendon, concentric, tube, endoscop...   
2    [magnetic, soft, actuation, magnetically, liqu...   
3    [path, rrt, planning, colony, ant, algorithm, ...   
4    [fish, swimming, underwater, fin, fins, propul...   
..                                                 ...   
270  [mxene, strain, mxenes, stretchable, conductiv...   
271  [malate, genes, crispr, tomato, genome, editin...   
272  [brain, fnirs, notifications, eog, bci, eeg, i...   
273  [exosuit, ule, shoulder, elbow, wearable, tsrs...   
274  [symmetrical, hypersonic, dbp, glide, reasonin...   

                                   Representative_Docs  
0    [The CARESSES study protocol: testing and eval...  
1    [Design, Modeling and Validation of a Tendon-D...  
2    [Bio-inspired physical intelligence for soft r...  
3    [Hybrid Path Planning Model for Multiple Robot...  
4    [Design and Mechanics of a Composite Wave-driv...  
..                                                 ...  
270  [Hierarchically buckled Ti<sub>3</sub>C<sub>2<...  
271  [Exploring the influence of a single-nucleotid...  
272  [A Novel Safety Evaluation Approach of Transfe...  
273  [A Cable-Driven Exosuit for Upper Limb Flexion...  
274  [Collaborative Autonomy: Human-Robot Interacti...  

[275 rows x 5 columns]

In [48]:
# Document information. Including the topic assignation
test = topic_model.get_document_info(docs, df = full_corpus)
test = test[['cluster', 'Name']].drop_duplicates(subset=['cluster'], keep='first')
print(test.shape)
test.head(10)

(275, 2)


cluster                                      Name
0      RBT-1-1---        1_continuum_tendon_concentric_tube
1134   RBT-1-2---    2_magnetic_soft_actuation_magnetically
2233   RBT-1-3---            4_fish_swimming_underwater_fin
3243   RBT-1-4---           13_soft_healing_jamming_gripper
3968   RBT-1-5---           18_tactile_skin_gripper_sensing
4645   RBT-1-6---        24_soft_koopman_continuum_modeling
5249   RBT-1-7---  36_tensegrity_crawling_origami_earthworm
5751   RBT-1-8---      62_endoscope_palpation_dvrk_suturing
6100   RBT-1-9---        84_snake_wormesh_snakes_locomotion
6389  RBT-1-10---      85_bioprinting_wearable_textile_soft



---



In [49]:
# Default
# Visualize topic similarity using heatmap (self similarity)
hm = topic_model.visualize_heatmap()
#hm.write_html(f"{ROOT_FOLDER_PATH}/heatmap_updated.html")
hm

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'coloraxis': 'coloraxis',
              'hovertemplate': 'x: %{x}<br>y: %{y}<br>Similarity Score: %{z}<extra></extra>',
              'name': '0',
              'type': 'heatmap',
              'x': [0_older_care_adults, 1_continuum_tendon_concentric,
                    2_magnetic_soft_actuation, ..., 272_brain_fnirs_notifications,
                    273_exosuit_ule_shoulder, 274_symmetrical_hypersonic_...],
              'xaxis': 'x',
              'y': [0_older_care_adults, 1_continuum_tendon_concentric,
                    2_magnetic_soft_actuation, ..., 272_brain_fnirs_notifications,
                    273_exosuit_ule_shoulder, 274_symmetrical_hypersonic_...],
              'yaxis': 'y',
              'z': array([[0.99999976, 0.53030276, 0.489552  , ..., 0.48305044, 0.47020417,
                           0.69260925],
                          [0.53030276, 0.9999999 , 0.80771345, ..., 0.20934132, 0.70142114,
                           0.44816172],
                          [0.489552  , 0.80771345, 1.0000001 , ..., 0.17910162, 0.69936436,
                           0.38227165],
                          ...,
                          [0.48305044, 0.20934132, 0.17910162, ..., 1.0000002 , 0.36942577,
                           0.55422354],
                          [0.47020417, 0.70142114, 0.69936436, ..., 0.36942577, 1.        ,
                           0.33131135],
                          [0.69260925, 0.44816172, 0.38227165, ..., 0.55422354, 0.33131135,
                           1.0000004 ]], dtype=float32)}],
    'layout': {'coloraxis': {'colorbar': {'title': {'text': 'Similarity Score'}},
                             'colorscale': [[0.0, 'rgb(247,252,240)'], [0.125,
                                            'rgb(224,243,219)'], [0.25,
                                            'rgb(204,235,197)'], [0.375,
                                            'rgb(168,221,181)'], [0.5,
                                            'rgb(123,204,196)'], [0.625,
                                            'rgb(78,179,211)'], [0.75,
                                            'rgb(43,140,190)'], [0.875,
                                            'rgb(8,104,172)'], [1.0,
                                            'rgb(8,64,129)']]},
               'height': 800,
               'hoverlabel': {'bgcolor': 'white', 'font': {'family': 'Rockwell', 'size': 16}},
               'legend': {'title': {'text': 'Trend'}},
               'margin': {'t': 60},
               'showlegend': True,
               'template': '...',
               'title': {'font': {'color': 'Black', 'size': 22},
                         'text': '<b>Similarity Matrix</b>',
                         'x': 0.55,
                         'xanchor': 'center',
                         'y': 0.95,
                         'yanchor': 'top'},
               'width': 800,
               'xaxis': {'anchor': 'y', 'constrain': 'domain', 'domain': [0.0, 1.0], 'scaleanchor': 'y'},
               'yaxis': {'anchor': 'x', 'autorange': 'reversed', 'constrain': 'domain', 'domain': [0.0, 1.0]}}
})

In [81]:
#pd.DataFrame(hm.data[0]['z'], columns=hm.data[0]['x']).to_csv(f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}/heatmap_matrix.csv', index=False)



---



## coordinates

In [50]:
import numpy as np
import umap

def reduce_dimensionality(data):
    # Create a UMAP object with the desired settings
    reducer = umap.UMAP(n_components=2, random_state=heatmap_settings['global']['seed'])

    # Perform dimensionality reduction
    reduced_data = reducer.fit_transform(data)

    return reduced_data

In [51]:
# Reduce dimensionality using UMAP
reduced_data = reduce_dimensionality(hm.data[0]['z'])
# Print the shape of the reduced data
print("Reduced data shape:", reduced_data.shape)

OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


Reduced data shape: (275, 2)


In [52]:
dms = pd.DataFrame(reduced_data)
dms.columns = ['x', 'y']
dms['label'] = tm_summary['Name']
dms['cluster'] = dms['label'].map(test.set_index('Name')['cluster'])
dms.head()

x          y                                   label     cluster
0  10.521773   5.051452            0_older_care_adults_dementia  RBT-2-1---
1   9.853635  10.925343      1_continuum_tendon_concentric_tube  RBT-1-1---
2   9.524106  11.100506  2_magnetic_soft_actuation_magnetically  RBT-1-2---
3   7.514737   6.395499              3_path_rrt_planning_colony  RBT-3-1---
4   9.498377  10.821355          4_fish_swimming_underwater_fin  RBT-1-3---

In [55]:
# Save dms
dms.to_csv(f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}/coordinates.csv', index = False)

In [56]:
# Save heatmap
pd.DataFrame(hm.data[0]['z'], columns=dms["cluster"]).to_csv(f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}/heatmap_matrix.csv', index=False)



---



## Melted

In [57]:
# prompt: `hm_test` is a squared matrix similarity matrix. This is a symmetric matrix so we only consider the lower triangle, without the diagonal.  Let's get the melted form as a data frame with 3 columns `Source`, `Target`, and `Similarity`. Then, sort it from the largest similarity to the lowest. Remove the pairs with value of zero.
hm_test = hm.data[0]['z']

# Assuming hm_test is your similarity matrix
df = pd.DataFrame(hm_test)

# Get the lower triangle without the diagonal
rows, cols = np.tril_indices(df.shape[0], -1)

# Create a DataFrame with Source, Target, and Similarity
similarity_df = pd.DataFrame({
    'Source': df.columns[rows],
    'Target': df.columns[cols],
    'Similarity': df.values[rows, cols]
})

# Remove rows with similarity of zero
similarity_df = similarity_df[similarity_df['Similarity'] > 0]

# Sort by similarity in descending order
similarity_df = similarity_df.sort_values('Similarity', ascending=False)

similarity_df

Source  Target  Similarity
10207     143      54    0.981928
11003     148     125    0.978769
37382     273     254    0.976255
8943      134      32    0.974429
21002     205      92    0.972784
...       ...     ...         ...
15085     174      34    0.000128
35657     267     146    0.000105
16841     184       5    0.000090
19441     197     135    0.000067
19392     197      86    0.000014

[35949 rows x 3 columns]

In [58]:
# prompt: Using dataframe similarity_df: Replace the values of columns Source and Target with the labels from `dms["cluster"]`

# Replace Source and Target with labels from dms["cluster"]
similarity_df['Source'] = similarity_df['Source'].map(lambda x: dms["cluster"][int(x)]) # Convert x to integer
similarity_df['Target'] = similarity_df['Target'].map(lambda x: dms["cluster"][int(x)]) # Convert x to integer


In [59]:
similarity_df.head(100)

Source        Target  Similarity
10207    RBT-9-7---    RBT-9-3---    0.981928
11003  RBT-99-16---    HA-8-99---    0.978769
37382     HA-2-4---     HA-2-3---    0.976255
8943     RBT-6-9---    RBT-6-3---    0.974429
21002  RBT-10-11---   RBT-10-2---    0.972784
...             ...           ...         ...
19802   RBT-11-5---   RBT-11-2---    0.939210
146     RBT-4-99---  RBT-99-99---    0.939174
32314     HA-2-3---     HA-2-1---    0.938739
6149     RBT-6-7---   RBT-6-99---    0.938729
2693    RBT-3-10---    RBT-3-7---    0.938664

[100 rows x 3 columns]

In [60]:
# # prompt: Using dataframe similarity_df: Replace the values of columns Source and Target with the corresponding "cluster" in the `dms` data frame. Use the column "label" in `dms` to find the matches.

# # Assuming you have a dataframe named 'dms' with 'label' and 'cluster' columns

# # Create a dictionary mapping 'label' to 'cluster' from the 'dms' dataframe
# label_to_cluster = dict(zip(dms['label'], dms['cluster']))

# # Replace 'Source' column values with corresponding 'cluster' values
# similarity_df['Source'] = similarity_df['Source'].map(label_to_cluster)

# # Replace 'Target' column values with corresponding 'cluster' values
# similarity_df['Target'] = similarity_df['Target'].map(label_to_cluster)

# similarity_df.head()

In [61]:
similarity_df.to_csv(f'{ROOT_FOLDER_PATH}/{heatmap_settings["metadata"]["heatmap_analysis_id"]}/heatmap_melted.csv', index = False)